### Imports

In [53]:
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV, KFold
from sklearn.linear_model import LinearRegression, Lasso, Ridge
from sklearn.multioutput import MultiOutputRegressor
from sklearn.neighbors import KNeighborsRegressor 
from sklearn.tree import DecisionTreeRegressor 
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.ensemble import BaggingRegressor, RandomForestRegressor, AdaBoostRegressor, GradientBoostingRegressor
from sklearn.pipeline import Pipeline
import statsmodels.api as sm
from sklearn import metrics

### Modeling -  Y = Excess Deaths

#### Model 1 - Benchmark

In [56]:
X = merged_data.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022'])
y = merged_data[['Exc_deaths_2021']]

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42)

In [57]:
lr1 = LinearRegression()
lr1.fit(X_train, y_train)

LinearRegression()

In [58]:
lr1.score(X_train, y_train)

1.0

In [59]:
lr1.score(X_test, y_test)

-1.9669490347275214

#### Model 2

In [60]:
sc = StandardScaler()
X_train_sc = sc.fit_transform(X_train)
X_test_sc = sc.transform(X_test)

In [61]:
lr2 = LinearRegression()
lr2.fit(X_train_sc, y_train)

LinearRegression()

In [62]:
lr2.score(X_train_sc, y_train), lr2.score(X_test_sc, y_test)

(1.0, 0.3771377100198612)

#### Model 3

In [63]:
knn = KNeighborsRegressor()
knn.fit(X_train, y_train)
knn.score(X_train, y_train), knn.score(X_test, y_test)

(0.7061358653697374, 0.7070898739868592)

#### Model 4

In [64]:
knn2 = KNeighborsRegressor()
knn2.fit(X_train_sc, y_train)
knn2.score(X_train_sc, y_train), knn2.score(X_test_sc, y_test)

(0.606112479485353, 0.3430513444405179)

#### Model 5

In [65]:
tree = DecisionTreeRegressor()
tree.fit(X_train, y_train)
tree.score(X_train, y_train), tree.score(X_test, y_test)

(1.0, 0.8856348202618944)

#### Model 6

In [66]:
tree2 = DecisionTreeRegressor()
tree2.fit(X_train_sc, y_train)
tree2.score(X_train_sc, y_train), tree2.score(X_test_sc, y_test)

(1.0, 0.8846859164405231)

#### Model 7 

In [67]:
bag1 = BaggingRegressor()
bag1.fit(X_train , y_train)
bag1.score(X_train, y_train), bag1.score(X_test, y_test)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_bagging.py:509: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return column_or_1d(y, warn=True)


(0.9018458363849775, 0.676719659204668)

#### Model 8

In [68]:
bag2 = BaggingRegressor()
bag2.fit(X_train_sc, y_train)
bag2.score(X_train_sc, y_train), bag2.score(X_test_sc, y_test)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_bagging.py:509: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return column_or_1d(y, warn=True)


(0.8907646106595325, 0.7536519166852861)

#### Model 9

In [69]:
rf1 = RandomForestRegressor()
rf1.fit(X_train, y_train)
rf1.score(X_train, y_train), rf1.score(X_test, y_test)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:1151: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


(0.9217019092312632, 0.6946731463832816)

#### Model 10

In [70]:
rf2 = RandomForestRegressor()
rf2.fit(X_train_sc, y_train)
rf2.score(X_train_sc, y_train), rf2.score(X_test_sc,y_test)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:1151: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


(0.9284383216318816, 0.589911823812978)

## Modelling - Y = Covid deaths

In [134]:
df = pd.read_csv('Data/merged_state_with_health.csv')
df.head()

Location  Employment_2020  Employment_2021  Employment_2022  \
0     Alabama          2671005          2769464          2869931   
1      Alaska           430840           443047           457687   
2     Arizona          3920033          4086802          4287595   
3    Arkansas          1639829          1686444          1755536   
4  California         23154091         23934549         25300974   

   Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  Life_Exp_2020  \
0             45887             50059             50916           73.2   
1             61898             65662             68635           76.6   
2             52133             56420             58442           76.3   
3             47147             51636             52618           73.8   
4             70061             76991             77036           79.0   

   Life_Exp_2019  Life_Exp_2018  Employer_2019  Non-Group_2019  Medicaid_2019  \
0           75.2           75.1          0.472           0.055          0.195   
1           77.7           78.0          0.484           0.035          0.213   
2           78.8           78.7          0.451           0.052          0.210   
3           75.7           75.6          0.420           0.054          0.262   
4           80.9           80.8          0.480           0.066          0.253   

   Medicare_2019  Military_2019  Uninsured_2019  Employer_2021  \
0          0.160          0.021           0.097          0.466   
1          0.100          0.053           0.115          0.433   
2          0.161          0.015           0.111          0.450   
3          0.159          0.014           0.091          0.411   
4          0.114          0.009           0.078          0.470   

   Non-Group_2021  Medicaid_2021  Medicare_2021  Military_2021  \
0           0.060          0.192          0.162          0.021   
1           0.041          0.257          0.107          0.053   
2           0.054          0.213          0.162          0.015   
3           0.056          0.270          0.156          0.015   
4           0.070          0.265          0.117          0.008   

   Uninsured_2021 Population Density per mi²  2010 Population  \
0           0.100                     100.65          4779736   
1           0.108                        1.3           710231   
2           0.106                      64.96          6392017   
3           0.092                      58.43          2915918   
4           0.070                     258.21         37253956   

   2020 Population  flu_vaccination_rate_2019  asthma_prevalence  \
0          5024279                       39.5                9.4   
1           733391                       37.0                9.7   
2          7151502                       37.1                9.8   
3          3011524                       40.1                9.3   
4         39538223                       40.7                7.8   

   cardiac_mortality_rate  high_bp_prevalence  copd_prevalence  \
0                   289.3                39.4              9.3   
1                   178.5                32.8              4.6   
2                   181.8                29.9              6.0   
3                   284.3                38.2              9.7   
4                   192.5                26.6              4.2   

   kidney_disease_prevalence  diabetes_prevalence Physicians  Physicians Rate  \
0                        3.1                 12.2     10,983            224.0   
1                        1.8                  7.1      2,101            287.2   
2                        3.6                  9.8     18,343            252.0   
3                        3.7                 12.2      6,500            215.4   
4                        2.8                  9.4    113,718            287.8   

  Active MO  Active MO Rate Active DO  Active DO Rate  Exc_deaths_2017  \
0    10,389           211.9       594            12.1             2649   
1     1,825           249.5       276 

In [135]:
df = df.merge(deaths_covid, on='Location')
df.head()

Location  Employment_2020  Employment_2021  Employment_2022  \
0     Alabama          2671005          2769464          2869931   
1      Alaska           430840           443047           457687   
2     Arizona          3920033          4086802          4287595   
3    Arkansas          1639829          1686444          1755536   
4  California         23154091         23934549         25300974   

   Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  Life_Exp_2020  \
0             45887             50059             50916           73.2   
1             61898             65662             68635           76.6   
2             52133             56420             58442           76.3   
3             47147             51636             52618           73.8   
4             70061             76991             77036           79.0   

   Life_Exp_2019  Life_Exp_2018  Employer_2019  Non-Group_2019  Medicaid_2019  \
0           75.2           75.1          0.472           0.055          0.195   
1           77.7           78.0          0.484           0.035          0.213   
2           78.8           78.7          0.451           0.052          0.210   
3           75.7           75.6          0.420           0.054          0.262   
4           80.9           80.8          0.480           0.066          0.253   

   Medicare_2019  Military_2019  Uninsured_2019  Employer_2021  \
0          0.160          0.021           0.097          0.466   
1          0.100          0.053           0.115          0.433   
2          0.161          0.015           0.111          0.450   
3          0.159          0.014           0.091          0.411   
4          0.114          0.009           0.078          0.470   

   Non-Group_2021  Medicaid_2021  Medicare_2021  Military_2021  \
0           0.060          0.192          0.162          0.021   
1           0.041          0.257          0.107          0.053   
2           0.054          0.213          0.162          0.015   
3           0.056          0.270          0.156          0.015   
4           0.070          0.265          0.117          0.008   

   Uninsured_2021 Population Density per mi²  2010 Population  \
0           0.100                     100.65          4779736   
1           0.108                        1.3           710231   
2           0.106                      64.96          6392017   
3           0.092                      58.43          2915918   
4           0.070                     258.21         37253956   

   2020 Population  flu_vaccination_rate_2019  asthma_prevalence  \
0          5024279                       39.5                9.4   
1           733391                       37.0                9.7   
2          7151502                       37.1                9.8   
3          3011524                       40.1                9.3   
4         39538223                       40.7                7.8   

   cardiac_mortality_rate  high_bp_prevalence  copd_prevalence  \
0                   289.3                39.4              9.3   
1                   178.5                32.8              4.6   
2                   181.8                29.9              6.0   
3                   284.3                38.2              9.7   
4                   192.5                26.6              4.2   

   kidney_disease_prevalence  diabetes_prevalence Physicians  Physicians Rate  \
0                        3.1                 12.2     10,983            224.0   
1                        1.8                  7.1      2,101            287.2   
2                        3.6                  9.8     18,343            252.0   
3                        3.7                 12.2      6,500            215.4   
4                        2.8                  9.4    113,718            287.8   

  Active MO  Active MO Rate Active DO  Active DO Rate  Exc_deaths_2017  \
0    10,389           211.9       594            12.1             2649   
1     1,825           249.5       276 

In [136]:
#df.drop('Mask_Mandate', inplace = True)
df['Population Density per mi²'] = df['Population Density per mi²'].str.replace(',', '', regex=True).astype(float)
df['Physicians'] = df['Physicians'].str.replace(',', '', regex=True).astype(float)
df['Active DO'] = df['Active DO'].str.replace(',', '', regex=True).astype(float)
df['Active MO'] = df['Active MO'].str.replace(',', '', regex=True).astype(float)
df['Mandatory'] = df['Mandatory'].map({'Yes':1, 'No':0})

In [306]:
df.to_csv('Data/merged_state_final.csv', index=False)

In [74]:
X1 = df.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y1 = df[['covid_2020', 'covid_2021', 'covid_2022']]

In [75]:
X1_train, X1_test, y1_train, y1_test = train_test_split(X1, y1, random_state=42)

In [76]:
sc = StandardScaler()
X1_train_sc = sc.fit_transform(X1_train)
X1_test_sc = sc.transform(X1_test)

#### Model 1

In [77]:
lr3 = LinearRegression()
lr3.fit(X1_train, y1_train)
lr3.score(X1_train, y1_train), lr3.score(X1_test, y1_test)

(1.0, 0.8804713015012814)

#### Model 2

In [78]:
lr4 = LinearRegression()
lr4.fit(X1_train_sc, y1_train)
lr4.score(X1_train_sc, y1_train), lr4.score(X1_test_sc, y1_test)

(1.0, 0.9133207097355621)

#### Model 3

In [79]:
knn3 = KNeighborsRegressor()
knn3.fit(X1_train, y1_train)
knn3.score(X1_train, y1_train), knn3.score(X1_test, y1_test)

(0.7791424748373533, 0.6836087417832482)

#### Model 4

In [80]:
knn4 = KNeighborsRegressor()
knn4.fit(X1_train_sc, y1_train)
knn4.score(X1_train_sc, y1_train), knn4.score(X1_test_sc, y1_test)

(0.6966822172725827, 0.4383678724517098)

#### Model 5

In [81]:
bag3 = BaggingRegressor()
bag3.fit(X1_train, y1_train)
bag3.score(X1_train, y1_train), bag3.score(X1_test, y1_test)

(0.9521687067303682, 0.6996976023899467)

#### Model 6

In [82]:
bag4 = BaggingRegressor()
bag4.fit(X1_train_sc, y1_train)
bag4.score(X1_train_sc, y1_train), bag4.score(X1_test_sc, y1_test)

(0.9086042950564988, 0.635067554907139)

#### Model 7

In [83]:
rf3 = RandomForestRegressor()
rf3.fit(X1_train, y1_train)
rf3.score(X1_train, y1_train), rf3.score(X1_test, y1_test)

(0.9395362659142088, 0.7178368263503238)

#### Model 8

In [84]:
rf4 = RandomForestRegressor()
rf4.fit(X1_train_sc, y1_train)
rf4.score(X1_train_sc, y1_train), rf4.score(X1_test_sc, y1_test)

(0.9418015871880029, 0.7435688596555051)

## Modeling - Y= Covid Deaths /population *100

In [85]:
X2 = df.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y2 = df[['Covid_pop_perce_2020', 'Covid_pop_perce_2021','Covid_pop_perce_2022']]

In [86]:
X2_train, X2_test, y2_train, y2_test = train_test_split(X2, y2, random_state=42)

In [87]:
sc2 = StandardScaler()
X2_train_sc = sc2.fit_transform(X2_train)
X2_test_sc = sc2.transform(X2_test)

#### Model 1

In [88]:
lr5 = LinearRegression()
lr5.fit(X2_train, y2_train)
lr5.score(X2_train, y2_train), lr5.score(X2_test, y2_test)

(1.0, -3.7498268302016293)

#### Model 2

In [89]:
lr6 = LinearRegression()
lr6.fit(X2_train_sc, y2_train)
lr6.score(X2_train_sc, y2_train), lr6.score(X2_test_sc, y2_test)

(1.0, -1.5764986241421983)

#### Model 3

In [90]:
knn5 = KNeighborsRegressor()
knn5.fit(X2_train, y2_train)
knn5.score(X2_train, y2_train), knn5.score(X2_test, y2_test)

(0.28285203212024396, -0.5384576466021559)

#### Model 4

In [91]:
knn6 = KNeighborsRegressor()
knn6.fit(X2_train_sc, y2_train)
knn6.score(X2_train_sc, y2_train), knn6.score(X2_test_sc, y2_test)

(0.6721761969412126, 0.15969089531059724)

#### Model 5

In [92]:
bag5 = BaggingRegressor()
bag5.fit(X2_train, y2_train)
bag5.score(X2_train, y2_train), bag5.score(X2_test, y2_test)

(0.8876063457098837, -0.05792069455125034)

#### Model 6

In [93]:
bag6 = BaggingRegressor()
bag6.fit(X2_train_sc, y2_train)
bag6.score(X2_train_sc, y2_train), bag6.score(X2_test_sc, y2_test)

(0.8813350713306285, 0.11297234394180163)

#### Model 7

In [94]:
rf5 = RandomForestRegressor()
rf5.fit(X2_train, y2_train)
rf5.score(X2_train, y2_train), rf5.score(X2_test, y2_test)

(0.9144070559104729, 0.11060293025620109)

#### Model 8

In [95]:
rf6 = RandomForestRegressor()
rf6.fit(X2_train_sc, y2_train)
rf6.score(X2_train_sc, y2_train), rf6.score(X2_test_sc, y2_test)

(0.9176042557209413, 0.09439234458967076)

# Model Tuning

## Y variable is covid deaths

In [96]:
df.head()

Location  Employment_2020  Employment_2021  Employment_2022  \
0     Alabama          2671005          2769464          2869931   
1      Alaska           430840           443047           457687   
2     Arizona          3920033          4086802          4287595   
3    Arkansas          1639829          1686444          1755536   
4  California         23154091         23934549         25300974   

   Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  Life_Exp_2020  \
0             45887             50059             50916           73.2   
1             61898             65662             68635           76.6   
2             52133             56420             58442           76.3   
3             47147             51636             52618           73.8   
4             70061             76991             77036           79.0   

   Life_Exp_2019  Life_Exp_2018  Employer_2019  Non-Group_2019  Medicaid_2019  \
0           75.2           75.1          0.472           0.055          0.195   
1           77.7           78.0          0.484           0.035          0.213   
2           78.8           78.7          0.451           0.052          0.210   
3           75.7           75.6          0.420           0.054          0.262   
4           80.9           80.8          0.480           0.066          0.253   

   Medicare_2019  Military_2019  Uninsured_2019  Employer_2021  \
0          0.160          0.021           0.097          0.466   
1          0.100          0.053           0.115          0.433   
2          0.161          0.015           0.111          0.450   
3          0.159          0.014           0.091          0.411   
4          0.114          0.009           0.078          0.470   

   Non-Group_2021  Medicaid_2021  Medicare_2021  Military_2021  \
0           0.060          0.192          0.162          0.021   
1           0.041          0.257          0.107          0.053   
2           0.054          0.213          0.162          0.015   
3           0.056          0.270          0.156          0.015   
4           0.070          0.265          0.117          0.008   

   Uninsured_2021  Population Density per mi²  2010 Population  \
0           0.100                      100.65          4779736   
1           0.108                        1.30           710231   
2           0.106                       64.96          6392017   
3           0.092                       58.43          2915918   
4           0.070                      258.21         37253956   

   2020 Population  flu_vaccination_rate_2019  asthma_prevalence  \
0          5024279                       39.5                9.4   
1           733391                       37.0                9.7   
2          7151502                       37.1                9.8   
3          3011524                       40.1                9.3   
4         39538223                       40.7                7.8   

   cardiac_mortality_rate  high_bp_prevalence  copd_prevalence  \
0                   289.3                39.4              9.3   
1                   178.5                32.8              4.6   
2                   181.8                29.9              6.0   
3                   284.3                38.2              9.7   
4                   192.5                26.6              4.2   

   kidney_disease_prevalence  diabetes_prevalence  Physicians  \
0                        3.1                 12.2     10983.0   
1                        1.8                  7.1      2101.0   
2                        3.6                  9.8     18343.0   
3                        3.7                 12.2      6500.0   
4                        2.8                  9.4    113718.0   

   Physicians Rate  Active MO  Active MO Rate  Active DO  Active DO Rate  \
0            224.0    10389.0           211.9      594.0            12.1   
1            287.2     1825.0           249.5      276.0            37.7   
2            252.0    15989.0           219.7   

In [97]:
X1 = df.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y1 = df[['covid_2020', 'covid_2021', 'covid_2022']]

In [98]:
X_train, X_test, y_train, y_test = train_test_split(X1, y1, random_state=42)

#### Model 1 - SS & Poly (RandomForest)

In [99]:
poly = PolynomialFeatures()
X_trainpoly = poly.fit_transform(X_train)
X_testpoly = poly.transform(X_test)

ss = StandardScaler()
X_train_polysc = ss.fit_transform(X_trainpoly)
X_test_polysc = ss.transform(X_testpoly)

In [100]:
rf = RandomForestRegressor()
rf.fit(X_train_polysc, y_train)
rf.score(X_train_polysc, y_train), rf.score(X_test_polysc, y_test)

(0.950687977951414, 0.7612151449978831)

#### Model 2 - SS & Poly (bagging)

In [101]:
bag = BaggingRegressor()
bag.fit(X_train_polysc, y_train)
bag.score(X_train_polysc, y_train), bag.score(X_test_polysc, y_test)

(0.9194340164271573, 0.7105364675682658)

#### Model 3 - SS & Poly (KNN)

In [297]:
knn = KNeighborsRegressor()
knn.fit(X_train_polysc, y_train)
knn.score(X_train_polysc, y_train), knn.score(X_test_polysc, y_test)

(0.7436503805578066, 0.5625614945672842)

#### Model 4 - SS, Poly, RF, Boosting + Gridsearch

In [321]:
base_rf = RandomForestRegressor()
adaboost_rf = AdaBoostRegressor(base_rf)
multi = MultiOutputRegressor(adaboost_rf)

params = {
    'estimator__n_estimators': [10, 100, 200], 
    'estimator__base_estimator__n_estimators': [50, 100], 
    'estimator__learning_rate': [0.1, 1, 10]  
}

kf = KFold(n_splits=10, shuffle=True, random_state=42)
gs = GridSearchCV(multi, params, cv=kf, n_jobs=-1)

In [322]:
%%time
gs.fit(X_train_polysc, y_train)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring for more details.
  valid_params[key].set_params(**sub_params)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring for more details.
  valid_params[key].set_params(**sub_params)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring for more details.
  valid_params[key].set_params(**sub_params)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring

CPU times: user 1min 8s, sys: 402 ms, total: 1min 8s
Wall time: 2h 4min 25s


GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=MultiOutputRegressor(estimator=AdaBoostRegressor(estimator=RandomForestRegressor())),
             n_jobs=-1,
             param_grid={'estimator__base_estimator__n_estimators': [50, 100],
                         'estimator__learning_rate': [0.1, 1, 10],
                         'estimator__n_estimators': [10, 100, 200]})

In [323]:
gs.score(X_train_polysc, y_train), gs.score(X_test_polysc, y_test)

(0.9615903661255262, 0.7842375910678697)

In [324]:
gs.best_params_

{'estimator__base_estimator__n_estimators': 100,
 'estimator__learning_rate': 0.1,
 'estimator__n_estimators': 10}

#### Model 5 - Poly, SS, Bagging, GradBoost & GridSearch

In [274]:
grad = GradientBoostingRegressor()
multi1 = MultiOutputRegressor(grad)

pgrid = {
    'estimator__learning_rate': [0.1, 1, 10],
    'estimator__n_estimators': [10, 100, 200],
    'estimator__max_depth': [None, 1, 2, 3]
}

kf1 = KFold(n_splits=10, shuffle=True, random_state=42)
gs1 = GridSearchCV(multi1, pgrid, cv=kf1, n_jobs=-1)

In [275]:
%%time
gs1.fit(X_train_polysc, y_train)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/co

CPU times: user 8.81 s, sys: 533 ms, total: 9.34 s
Wall time: 14min 32s


GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=MultiOutputRegressor(estimator=GradientBoostingRegressor()),
             n_jobs=-1,
             param_grid={'estimator__learning_rate': [0.1, 1, 10],
                         'estimator__max_depth': [None, 1, 2, 3],
                         'estimator__n_estimators': [10, 100, 200, 300]})

In [276]:
gs1.score(X_train_polysc, y_train), gs1.score(X_test_polysc, y_test)

(0.9999918872830208, 0.9182707938645693)

In [277]:
gs1.best_params_

{'estimator__learning_rate': 0.1,
 'estimator__max_depth': 1,
 'estimator__n_estimators': 200}

#### Model 5

In [332]:
params = {
    'max_features': np.arange(1, X.shape[1] + 1), 
    'max_depth': np.append(np.arange(1, 10), None), 
    'min_samples_leaf': np.arange(1, 31) 
}
kf = KFold(n_splits=10, shuffle=True, random_state=2023)
ranfor = RandomForestRegressor(
    n_estimators=100,
    random_state=2023
)

gs2 = GridSearchCV(ranfor, params, cv=kf, n_jobs=6)

In [334]:
%%time
gs2.fit(X_train_polysc, y_train)

CPU times: user 1min 57s, sys: 18.1 s, total: 2min 15s
Wall time: 33min 59s


GridSearchCV(cv=KFold(n_splits=10, random_state=2023, shuffle=True),
             estimator=RandomForestRegressor(random_state=2023), n_jobs=6,
             param_grid={'max_depth': array([1, 2, 3, 4, 5, 6, 7, 8, 9, None], dtype=object),
                         'max_features': array([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,
        14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,  26,
        27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,  39,
        40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,  52,
        53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,  65,
        66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,  78,
        79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,  91,
        92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103, 104,
       105, 106]),
                         'min_samples_leaf': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30])})

In [335]:
gs2.score(X_train_polysc, y_train), gs2.score(X_test_polysc, y_test)

(0.7930247825616247, 0.6592708754598661)

In [115]:
lr = LinearRegression()
lr.fit(X_train_polysc, y_train)
lr.score(X_train_polysc, y_train), lr.score(X_test_polysc, y_test)

(1.0, 0.9170538077072194)

### Y is Excess Deaths

In [102]:
X2 = df.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y2 = df[['Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022']]

In [103]:
X2_train, X2_test, y2_train, y2_test = train_test_split(X2, y2, random_state=42)

poly = PolynomialFeatures()
X2_train_poly = poly.fit_transform(X2_train)
X2_test_poly = poly.transform(X2_test)

sc = StandardScaler()
X2_train_polysc = sc.fit_transform(X2_train_poly)
X2_test_polysc = sc.transform(X2_test_poly)

#### Model 1

In [104]:
rf = RandomForestRegressor()
rf.fit(X2_train_polysc, y2_train)
rf.score(X2_train_polysc, y2_train), rf.score(X2_test_polysc, y2_test)

(0.9556624783950433, 0.6596390175802633)

#### Model 2

In [105]:
bag = BaggingRegressor()
bag.fit(X2_train_polysc, y2_train)
bag.score(X2_train_polysc, y2_train), bag.score(X2_test_polysc, y2_test)

(0.9668165467988512, 0.7742026379311312)

#### Model 3

In [112]:
base_rf = RandomForestRegressor()
adaboost_rf = AdaBoostRegressor(base_rf)
multi = MultiOutputRegressor(adaboost_rf)

params = {
    'estimator__n_estimators': [10, 100, 200], 
    'estimator__base_estimator__n_estimators': [50, 100], 
    'estimator__learning_rate': [0.1, 1, 10]  
}

kf = KFold(n_splits=10, shuffle=True, random_state=42)
gs = GridSearchCV(multi, params, cv=kf, n_jobs=-1)

In [113]:
%%time
gs.fit(X_train_polysc, y_train)


/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring for more details.
  valid_params[key].set_params(**sub_params)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring for more details.
  valid_params[key].set_params(**sub_params)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring for more details.
  valid_params[key].set_params(**sub_params)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/base.py:262: FutureWarning: Parameter 'base_estimator' of AdaBoostRegressor is deprecated in favor of 'estimator'. See AdaBoostRegressor's docstring

CPU times: user 33.2 s, sys: 309 ms, total: 33.5 s
Wall time: 2h 16min 19s


GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=MultiOutputRegressor(estimator=AdaBoostRegressor(estimator=RandomForestRegressor())),
             n_jobs=-1,
             param_grid={'estimator__base_estimator__n_estimators': [50, 100],
                         'estimator__learning_rate': [0.1, 1, 10],
                         'estimator__n_estimators': [10, 100, 200]})

In [114]:
gs.score(X_train_polysc, y_train), gs.score(X_test_polysc, y_test)

(0.9581031719495128, 0.7994069264987734)

#### Model 4

In [106]:
grad = GradientBoostingRegressor()
multi1 = MultiOutputRegressor(grad)

pgrid = {
    'estimator__learning_rate': [0.1, 1, 10],
    'estimator__n_estimators': [10, 100],
    'estimator__max_depth': [None, 1, 2, 3]
}

kf1 = KFold(n_splits=10, shuffle=True, random_state=42)
gs1 = GridSearchCV(multi1, pgrid, cv=kf1, n_jobs=-1)

In [107]:
%%time
gs1.fit(X_train_polysc, y_train)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/model_selection/_search.py:987: RuntimeWarning: overflow encountered in square
  (array - array_means[:, np.newaxis]) ** 2, axis=1, weights=weights


CPU times: user 3.96 s, sys: 117 ms, total: 4.08 s
Wall time: 2min 39s


GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=MultiOutputRegressor(estimator=GradientBoostingRegressor()),
             n_jobs=-1,
             param_grid={'estimator__learning_rate': [0.1, 1, 10],
                         'estimator__max_depth': [None, 1, 2, 3],
                         'estimator__n_estimators': [10, 100]})

In [108]:
gs1.score(X_train_polysc, y_train), gs1.score(X_test_polysc, y_test)

(0.9996712212524659, 0.9039638428509988)

#### Model 5

In [109]:
params = {
    'max_features': np.arange(1, X.shape[1] + 1), 
    'max_depth': np.append(np.arange(1, 10), None), 
    'min_samples_leaf': np.arange(1, 31) 
}
kf = KFold(n_splits=10, shuffle=True, random_state=2023)
ranfor = RandomForestRegressor(
    n_estimators=100,
    random_state=2023
)

gs2 = GridSearchCV(ranfor, params, cv=kf, n_jobs=-1)

In [110]:
%%time
gs2.fit(X_train_polysc, y_train)

CPU times: user 1min 1s, sys: 9.24 s, total: 1min 11s
Wall time: 21min 3s


GridSearchCV(cv=KFold(n_splits=10, random_state=2023, shuffle=True),
             estimator=RandomForestRegressor(random_state=2023), n_jobs=-1,
             param_grid={'max_depth': array([1, 2, 3, 4, 5, 6, 7, 8, 9, None], dtype=object),
                         'max_features': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34,
       35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51,
       52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63]),
                         'min_samples_leaf': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30])})

In [111]:
gs2.score(X_train_polysc, y_train), gs2.score(X_test_polysc, y_test)

(0.7930247825616247, 0.6592708754598661)

#### Base LR Models

In [137]:
X1 = df.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y1 = df[['covid_2020', 'covid_2021', 'covid_2022']]

In [138]:
X1_train, X1_test, y1_train, y1_test = train_test_split(X1, y1, random_state =42)

In [147]:
las = Lasso(max_iter=1000, alpha=0.1)
las.fit(X1_train, y1_train)
las.score(X1_train, y1_train), las.score(X1_test, y1_test)

(0.9999991400245168, 0.9226665134912698)

In [247]:
coef = pd.DataFrame(las.coef_.T).round(2)
var = pd.DataFrame(X1.columns).rename(columns={0:'Variables'})
pd.concat([var, coef], axis=1).rename(columns={0:2020, 1:2021, 2:2022})

Variables     2020      2021  \
0                                      Employment_2020     0.00      0.00   
1                                      Employment_2021     0.00      0.00   
2                                      Employment_2022    -0.00      0.00   
3                                     Inc_Per_Cap_2020     0.01     -0.17   
4                                     Inc_Per_Cap_2021    -0.00      0.04   
5                                     Inc_Per_CAp_2022     0.03      0.07   
6                                        Life_Exp_2020  -536.68   -864.95   
7                                        Life_Exp_2019  -148.22  -1488.71   
8                                        Life_Exp_2018  -125.09    113.67   
9                                        Employer_2019    -0.00     -0.00   
10                                      Non-Group_2019    -0.00      0.00   
11                                       Medicaid_2019     0.00 -29291.00   
12                                       Medicare_2019     0.00      0.00   
13                                       Military_2019     0.00      0.00   
14                                      Uninsured_2019     0.00  14483.32   
15                                       Employer_2021  -128.09 -22940.05   
16                                      Non-Group_2021    -0.00      0.00   
17                                       Medicaid_2021   283.78  -1952.98   
18                                       Medicare_2021     0.00      0.00   
19                                       Military_2021     0.00      0.00   
20                                      Uninsured_2021     0.00  16489.58   
21                          Population Density per mi²     4.29      6.20   
22                                     2010 Population    -0.00     -0.00   
23                                     2020 Population     0.00      0.00   
24                           flu_vaccination_rate_2019  -107.38      5.79   
25                                   asthma_prevalence   423.54   -314.85   
26                              cardiac_mortality_rate     4.67    -50.85   
27                                  high_bp_prevalence  -171.39     42.00   
28                                     copd_prevalence  -628.70     31.12   
29                           kidney_disease_prevalence   121.76   -152.86   
30                                 diabetes_prevalence   295.77   -440.04   
31                                          Physicians    -0.07     -0.13   
32                                     Physicians Rate     0.14     -6.14   
33                                           Active MO    -0.01     -0.01   
34                                      Active MO Rate    -0.21      0.67   
35                                           Active DO     0.81      1.83   
36                                      Active DO Rate   -16.50    -76.71   
37                                Dist_Per_100K_2021_x     0.00      0.06   
38                  Distributed_Per_100k_65Plus_2021_x     0.00     -0.00   
39                               Admin_Per_100K_2021_x     0.00      0.01   
40                        Admin_Per_100k_65Plus_2021_x     0.01      0.03   
41                   Administered_Dose1_Pop_Pct_2021_x   -29.38    -11.65   
42       Administered_Dose1_Recip_65PlusPop_Pct_2021_x   367.65    459.95   
43                      Series_Complete_Pop_Pct_2021_x   -81.90   -189.16   
44                Series_Complete_65PlusPop_Pct_2021_x    87.88    -89.42   
45                     Additional_Doses_Vax_Pct_2021_x    72.74    -95.18   
46              Additional_Doses_50Plus_Vax_Pct_2021_x   -12.16      3.40   
47              Additional_Doses_65Plus_Vax_Pct_2021_x    -3.57     -8.31   
48                                Dist_Per_100K_2022_x     0.01      0.03   
49                  Distributed_Per_100k_65Plus_2022_x     0.00     -0.00   
50                               Admin_Per_100K_2022_x    -0.01     -0.00   
51                        Admin_Per_100k_

In [153]:
rid = Ridge(max_iter=1000, alpha=0.1)
rid.fit(X1_train, y1_train)
rid.score(X1_train, y1_train), rid.score(X1_test, y1_test)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_ridge.py:248: LinAlgWarning: Ill-conditioned matrix (rcond=7.15002e-18): result may not be accurate.
  dual_coef = linalg.solve(K, y, assume_a="pos", overwrite_a=False)


(0.9999991019303627, 0.8806077277677167)

In [154]:
X2 = df.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y2 = df[['Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022']]

In [155]:
X2_train, X2_test, y2_train, y2_test = train_test_split(X2, y2, random_state=42)

In [164]:
las1 = Lasso(max_iter=1000, alpha=0.1)
las1.fit(X2_train, y2_train)
las1.score(X2_train, y2_train), las1.score(X2_test, y2_test)

(0.9999983098378628, 0.8926730135813484)

In [248]:
coef1 = pd.DataFrame(las1.coef_.T).round(2)
var1 = pd.DataFrame(X2.columns).rename(columns={0:'Variables'})
pd.concat([var1, coef1], axis=1).rename(columns={0:2020, 1:2021, 2:2022})

Variables      2020       2021  \
0                                      Employment_2020      0.01       0.01   
1                                      Employment_2021      0.00       0.00   
2                                      Employment_2022      0.00       0.00   
3                                     Inc_Per_Cap_2020     -0.12      -0.50   
4                                     Inc_Per_Cap_2021      0.05       0.10   
5                                     Inc_Per_CAp_2022      0.07       0.14   
6                                        Life_Exp_2020  -1970.66   -2929.77   
7                                        Life_Exp_2019   -150.63   -3468.06   
8                                        Life_Exp_2018   -145.98     321.23   
9                                        Employer_2019      0.00  -65931.23   
10                                      Non-Group_2019      0.00      -0.00   
11                                       Medicaid_2019  -9357.38  -97137.81   
12                                       Medicare_2019     -0.00       0.00   
13                                       Military_2019      0.00  104719.03   
14                                      Uninsured_2019  20068.79   34088.69   
15                                       Employer_2021     -0.00  -51375.78   
16                                      Non-Group_2021      0.00       0.00   
17                                       Medicaid_2021  -7530.19  -19681.23   
18                                       Medicare_2021     -0.00      -0.00   
19                                       Military_2021      0.00   33779.54   
20                                      Uninsured_2021      0.00    6553.00   
21                          Population Density per mi²     11.53      16.74   
22                                     2010 Population     -0.00      -0.00   
23                                     2020 Population      0.00       0.00   
24                           flu_vaccination_rate_2019   -445.18       1.08   
25                                   asthma_prevalence    959.55   -1168.49   
26                              cardiac_mortality_rate    -41.28    -168.60   
27                                  high_bp_prevalence    298.96     424.91   
28                                     copd_prevalence  -1596.58     503.09   
29                           kidney_disease_prevalence    220.03    -434.25   
30                                 diabetes_prevalence    400.81   -2017.09   
31                                          Physicians     -0.15      -0.26   
32                                     Physicians Rate     -2.21     -20.11   
33                                           Active MO     -0.02      -0.01   
34                                      Active MO Rate     -1.83       2.32   
35                                           Active DO      2.26       3.70   
36                                      Active DO Rate    -22.95    -187.54   
37                                Dist_Per_100K_2021_x     -0.03       0.17   
38                  Distributed_Per_100k_65Plus_2021_x      0.00      -0.00   
39                               Admin_Per_100K_2021_x      0.00       0.04   
40                        Admin_Per_100k_65Plus_2021_x      0.06       0.06   
41                   Administered_Dose1_Pop_Pct_2021_x   -116.10    -102.78   
42       Administered_Dose1_Recip_65PlusPop_Pct_2021_x    854.26    1006.73   
43                      Series_Complete_Pop_Pct_2021_x   -147.25    -326.21   
44                Series_Complete_65PlusPop_Pct_2021_x     66.46    -300.22   
45                     Additional_Doses_Vax_Pct_2021_x    146.60    -237.75   
46              Additional_Doses_50Plus_Vax_Pct_2021_x      5.70      10.35   
47              Additional_Doses_65Plus_Vax_Pct_2021_x    -16.36     -31.14   
48                                Dist_Per_100K_2022_x      0.02       0.07   
49                  Distributed_Per_100k_65Plus_2022_x      0.00       0.00   
50              

In [170]:
rid1 = Ridge(max_iter=8000, alpha=0.1)
rid1.fit(X2_train, y2_train)
rid1.score(X2_train, y2_train), rid1.score(X2_test, y2_test)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_ridge.py:248: LinAlgWarning: Ill-conditioned matrix (rcond=7.15002e-18): result may not be accurate.
  dual_coef = linalg.solve(K, y, assume_a="pos", overwrite_a=False)


(0.999999594752488, 0.8031595859109605)

## OLS

#### Covid Deaths

In [258]:
yols2020 = df['covid_2020']

ols12020 = sm.OLS((yols2020.astype(float)), (X2.astype(float))).fit()
ols12020.summary()

/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: divide by zero encountered in divide
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: invalid value encountered in scalar multiply
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1716: RuntimeWarning: divide by zero encountered in scalar divide
  return np.dot(wresid, wresid) / self.df_resid


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:             covid_2020   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Tue, 07 Nov 2023   Prob (F-statistic):                nan
Time:                        02:21:29   Log-Likelihood:                 830.34
No. Observations:                  50   AIC:                            -1561.
Df Residuals:                       0   BIC:                            -1465.
Df Model:                          49                                         
Covariance Type:            nonrobust                                         
===========================================================================================================================================
                                                                              coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------------------------------------------
Employment_2020                                                            -0.0049        inf         -0        nan         nan         nan
Employment_2021                                                             0.0378        inf          0        nan         nan         nan
Employment_2022                                                            -0.0300        inf         -0        nan         nan         nan
Inc_Per_Cap_2020                                                           -0.4989        inf         -0        nan         nan         nan
Inc_Per_Cap_2021                                                            1.3181        inf          0        nan         nan         nan
Inc_Per_CAp_2022                                                           -0.5156        inf         -0        nan         nan         nan
Life_Exp_2020                                                            -357.0972        inf         -0        nan         nan         nan
Life_Exp_2019                                                             132.7673        inf          0        nan         nan         nan
Life_Exp_2018                                                              87.4442        inf          0        nan         nan         nan
Employer_2019                                                               9.3521        inf          0        nan         nan         nan
Non-Group_2019                                                             -3.1271        inf         -0        nan         nan         nan
Medicaid_2019                                                               4.9995        inf          0        nan         nan         nan
Medicare_2019                                                              -4.5439        inf         -0        nan         nan         nan
Military_2019                                                              -5.6683        inf         -0        nan         nan         nan
Uninsured_2019                                                             -2.3694        inf         -0        nan         nan         nan
Employer_2021                                                               9.5225        inf          0        nan         nan         nan
Non-Group_2021                                                             -9.0169        inf         -0        nan         nan         nan
Medicaid_2021                                                               0.4947        inf          0        nan         nan         nan
Medicare_2021                                                              -2.4891        inf         -0        nan         nan         nan
Mil

In [259]:
yols2021 = df['covid_2021']

ols12021 = sm.OLS((yols2021.astype(float)), (X2.astype(float))).fit()
ols12021.summary()

/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: divide by zero encountered in divide
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: invalid value encountered in scalar multiply
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1716: RuntimeWarning: divide by zero encountered in scalar divide
  return np.dot(wresid, wresid) / self.df_resid


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:             covid_2021   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Tue, 07 Nov 2023   Prob (F-statistic):                nan
Time:                        02:21:32   Log-Likelihood:                 870.24
No. Observations:                  50   AIC:                            -1640.
Df Residuals:                       0   BIC:                            -1545.
Df Model:                          49                                         
Covariance Type:            nonrobust                                         
===========================================================================================================================================
                                                                              coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------------------------------------------
Employment_2020                                                             0.0149        inf          0        nan         nan         nan
Employment_2021                                                            -0.0138        inf         -0        nan         nan         nan
Employment_2022                                                             0.0015        inf          0        nan         nan         nan
Inc_Per_Cap_2020                                                            0.4708        inf          0        nan         nan         nan
Inc_Per_Cap_2021                                                           -1.0716        inf         -0        nan         nan         nan
Inc_Per_CAp_2022                                                            0.6027        inf          0        nan         nan         nan
Life_Exp_2020                                                            -165.4145        inf         -0        nan         nan         nan
Life_Exp_2019                                                             -97.2284        inf         -0        nan         nan         nan
Life_Exp_2018                                                            -158.1464        inf         -0        nan         nan         nan
Employer_2019                                                             -43.3618        inf         -0        nan         nan         nan
Non-Group_2019                                                              2.2559        inf          0        nan         nan         nan
Medicaid_2019                                                              32.0938        inf          0        nan         nan         nan
Medicare_2019                                                              -2.7507        inf         -0        nan         nan         nan
Military_2019                                                               5.0669        inf          0        nan         nan         nan
Uninsured_2019                                                              9.9583        inf          0        nan         nan         nan
Employer_2021                                                             -38.4963        inf         -0        nan         nan         nan
Non-Group_2021                                                              5.3507        inf          0        nan         nan         nan
Medicaid_2021                                                              32.9199        inf          0        nan         nan         nan
Medicare_2021                                                              -5.5491        inf         -0        nan         nan         nan
Mil

In [260]:
yols2022 = df['covid_2022']

ols12022 = sm.OLS((yols2022.astype(float)), (X2.astype(float))).fit()
ols12022.summary()

/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: divide by zero encountered in divide
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: invalid value encountered in scalar multiply
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1716: RuntimeWarning: divide by zero encountered in scalar divide
  return np.dot(wresid, wresid) / self.df_resid


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:             covid_2022   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Tue, 07 Nov 2023   Prob (F-statistic):                nan
Time:                        02:22:03   Log-Likelihood:                 879.00
No. Observations:                  50   AIC:                            -1658.
Df Residuals:                       0   BIC:                            -1562.
Df Model:                          49                                         
Covariance Type:            nonrobust                                         
===========================================================================================================================================
                                                                              coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------------------------------------------
Employment_2020                                                            -0.0013        inf         -0        nan         nan         nan
Employment_2021                                                             0.0088        inf          0        nan         nan         nan
Employment_2022                                                            -0.0026        inf         -0        nan         nan         nan
Inc_Per_Cap_2020                                                           -0.1804        inf         -0        nan         nan         nan
Inc_Per_Cap_2021                                                            0.5634        inf          0        nan         nan         nan
Inc_Per_CAp_2022                                                           -0.3658        inf         -0        nan         nan         nan
Life_Exp_2020                                                             -12.5379        inf         -0        nan         nan         nan
Life_Exp_2019                                                            -100.5055        inf         -0        nan         nan         nan
Life_Exp_2018                                                             -98.8060        inf         -0        nan         nan         nan
Employer_2019                                                              -6.3112        inf         -0        nan         nan         nan
Non-Group_2019                                                              0.0600        inf          0        nan         nan         nan
Medicaid_2019                                                               4.5011        inf          0        nan         nan         nan
Medicare_2019                                                              -0.3454        inf         -0        nan         nan         nan
Military_2019                                                               2.1102        inf          0        nan         nan         nan
Uninsured_2019                                                              0.7069        inf          0        nan         nan         nan
Employer_2021                                                              -4.3450        inf         -0        nan         nan         nan
Non-Group_2021                                                              1.3831        inf          0        nan         nan         nan
Medicaid_2021                                                               2.6623        inf          0        nan         nan         nan
Medicare_2021                                                              -0.8061        inf         -0        nan         nan         nan
Mil

#### Excess Deaths

In [261]:
y2ols2020 = df['Exc_deaths_2020']
ols12020 = sm.OLS((y2ols2020.astype(float)), (X2.astype(float))).fit()
ols12020.summary()

/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: divide by zero encountered in divide
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: invalid value encountered in scalar multiply
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1716: RuntimeWarning: divide by zero encountered in scalar divide
  return np.dot(wresid, wresid) / self.df_resid


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:        Exc_deaths_2020   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Tue, 07 Nov 2023   Prob (F-statistic):                nan
Time:                        02:25:15   Log-Likelihood:                 776.44
No. Observations:                  50   AIC:                            -1453.
Df Residuals:                       0   BIC:                            -1357.
Df Model:                          49                                         
Covariance Type:            nonrobust                                         
===========================================================================================================================================
                                                                              coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------------------------------------------
Employment_2020                                                            -0.0287        inf         -0        nan         nan         nan
Employment_2021                                                             0.1253        inf          0        nan         nan         nan
Employment_2022                                                            -0.1044        inf         -0        nan         nan         nan
Inc_Per_Cap_2020                                                           -1.4281        inf         -0        nan         nan         nan
Inc_Per_Cap_2021                                                            0.7480        inf          0        nan         nan         nan
Inc_Per_CAp_2022                                                            1.2454        inf          0        nan         nan         nan
Life_Exp_2020                                                           -1048.3467        inf         -0        nan         nan         nan
Life_Exp_2019                                                             383.9420        inf          0        nan         nan         nan
Life_Exp_2018                                                             198.9968        inf          0        nan         nan         nan
Employer_2019                                                             -17.4593        inf         -0        nan         nan         nan
Non-Group_2019                                                             -0.6987        inf         -0        nan         nan         nan
Medicaid_2019                                                              32.2971        inf          0        nan         nan         nan
Medicare_2019                                                             -10.5206        inf         -0        nan         nan         nan
Military_2019                                                             -12.3417        inf         -0        nan         nan         nan
Uninsured_2019                                                              9.7218        inf          0        nan         nan         nan
Employer_2021                                                             -11.9962        inf         -0        nan         nan         nan
Non-Group_2021                                                            -13.7499        inf         -0        nan         nan         nan
Medicaid_2021                                                              21.4666        inf          0        nan         nan         nan
Medicare_2021                                                              -7.6984        inf         -0        nan         nan         nan
Mil

In [262]:
y2ols2021 = df['Exc_deaths_2021']
ols12021 = sm.OLS((y2ols2021.astype(float)), (X2.astype(float))).fit()
ols12021.summary()

/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: divide by zero encountered in divide
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: invalid value encountered in scalar multiply
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1716: RuntimeWarning: divide by zero encountered in scalar divide
  return np.dot(wresid, wresid) / self.df_resid


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:        Exc_deaths_2021   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Tue, 07 Nov 2023   Prob (F-statistic):                nan
Time:                        02:25:55   Log-Likelihood:                 808.57
No. Observations:                  50   AIC:                            -1517.
Df Residuals:                       0   BIC:                            -1422.
Df Model:                          49                                         
Covariance Type:            nonrobust                                         
===========================================================================================================================================
                                                                              coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------------------------------------------
Employment_2020                                                             0.0048        inf          0        nan         nan         nan
Employment_2021                                                             0.0456        inf          0        nan         nan         nan
Employment_2022                                                            -0.0496        inf         -0        nan         nan         nan
Inc_Per_Cap_2020                                                            1.6164        inf          0        nan         nan         nan
Inc_Per_Cap_2021                                                           -4.1706        inf         -0        nan         nan         nan
Inc_Per_CAp_2022                                                            2.4134        inf          0        nan         nan         nan
Life_Exp_2020                                                             -81.2404        inf         -0        nan         nan         nan
Life_Exp_2019                                                             -95.1028        inf         -0        nan         nan         nan
Life_Exp_2018                                                            -293.8956        inf         -0        nan         nan         nan
Employer_2019                                                            -163.7513        inf         -0        nan         nan         nan
Non-Group_2019                                                             11.6024        inf          0        nan         nan         nan
Medicaid_2019                                                             122.6693        inf          0        nan         nan         nan
Medicare_2019                                                              -6.6347        inf         -0        nan         nan         nan
Military_2019                                                              16.1363        inf          0        nan         nan         nan
Uninsured_2019                                                             34.3802        inf          0        nan         nan         nan
Employer_2021                                                            -144.8158        inf         -0        nan         nan         nan
Non-Group_2021                                                             23.9910        inf          0        nan         nan         nan
Medicaid_2021                                                             129.7462        inf          0        nan         nan         nan
Medicare_2021                                                             -18.2736        inf         -0        nan         nan         nan
Mil

In [263]:
y2ols2022 = df['Exc_deaths_2022']
ols12022 = sm.OLS((y2ols2022.astype(float)), (X2.astype(float))).fit()
ols12022.summary()

/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: divide by zero encountered in divide
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1794: RuntimeWarning: invalid value encountered in scalar multiply
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/Users/anaconda3/lib/python3.11/site-packages/statsmodels/regression/linear_model.py:1716: RuntimeWarning: divide by zero encountered in scalar divide
  return np.dot(wresid, wresid) / self.df_resid


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:        Exc_deaths_2022   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Tue, 07 Nov 2023   Prob (F-statistic):                nan
Time:                        02:26:09   Log-Likelihood:                 826.79
No. Observations:                  50   AIC:                            -1554.
Df Residuals:                       0   BIC:                            -1458.
Df Model:                          49                                         
Covariance Type:            nonrobust                                         
===========================================================================================================================================
                                                                              coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------------------------------------------
Employment_2020                                                             0.0184        inf          0        nan         nan         nan
Employment_2021                                                             0.0070        inf          0        nan         nan         nan
Employment_2022                                                            -0.0202        inf         -0        nan         nan         nan
Inc_Per_Cap_2020                                                           -0.3531        inf         -0        nan         nan         nan
Inc_Per_Cap_2021                                                           -0.2706        inf         -0        nan         nan         nan
Inc_Per_CAp_2022                                                            0.5733        inf          0        nan         nan         nan
Life_Exp_2020                                                              56.4651        inf          0        nan         nan         nan
Life_Exp_2019                                                            -127.3124        inf         -0        nan         nan         nan
Life_Exp_2018                                                            -234.7820        inf         -0        nan         nan         nan
Employer_2019                                                             -87.0506        inf         -0        nan         nan         nan
Non-Group_2019                                                              6.6371        inf          0        nan         nan         nan
Medicaid_2019                                                              66.5903        inf          0        nan         nan         nan
Medicare_2019                                                              -1.8572        inf         -0        nan         nan         nan
Military_2019                                                               9.1141        inf          0        nan         nan         nan
Uninsured_2019                                                             15.5057        inf          0        nan         nan         nan
Employer_2021                                                             -76.3827        inf         -0        nan         nan         nan
Non-Group_2021                                                             14.1473        inf          0        nan         nan         nan
Medicaid_2021                                                              68.6894        inf          0        nan         nan         nan
Medicare_2021                                                              -7.7012        inf         -0        nan         nan         nan
Mil

# Model Testing and Analysis

## Creating Dummy data

In [266]:
df.head()

Location  Employment_2020  Employment_2021  Employment_2022  \
0     Alabama          2671005          2769464          2869931   
1      Alaska           430840           443047           457687   
2     Arizona          3920033          4086802          4287595   
3    Arkansas          1639829          1686444          1755536   
4  California         23154091         23934549         25300974   

   Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  Life_Exp_2020  \
0             45887             50059             50916           73.2   
1             61898             65662             68635           76.6   
2             52133             56420             58442           76.3   
3             47147             51636             52618           73.8   
4             70061             76991             77036           79.0   

   Life_Exp_2019  Life_Exp_2018  Employer_2019  Non-Group_2019  Medicaid_2019  \
0           75.2           75.1          0.472           0.055          0.195   
1           77.7           78.0          0.484           0.035          0.213   
2           78.8           78.7          0.451           0.052          0.210   
3           75.7           75.6          0.420           0.054          0.262   
4           80.9           80.8          0.480           0.066          0.253   

   Medicare_2019  Military_2019  Uninsured_2019  Employer_2021  \
0          0.160          0.021           0.097          0.466   
1          0.100          0.053           0.115          0.433   
2          0.161          0.015           0.111          0.450   
3          0.159          0.014           0.091          0.411   
4          0.114          0.009           0.078          0.470   

   Non-Group_2021  Medicaid_2021  Medicare_2021  Military_2021  \
0           0.060          0.192          0.162          0.021   
1           0.041          0.257          0.107          0.053   
2           0.054          0.213          0.162          0.015   
3           0.056          0.270          0.156          0.015   
4           0.070          0.265          0.117          0.008   

   Uninsured_2021  Population Density per mi²  2010 Population  \
0           0.100                      100.65          4779736   
1           0.108                        1.30           710231   
2           0.106                       64.96          6392017   
3           0.092                       58.43          2915918   
4           0.070                      258.21         37253956   

   2020 Population  flu_vaccination_rate_2019  asthma_prevalence  \
0          5024279                       39.5                9.4   
1           733391                       37.0                9.7   
2          7151502                       37.1                9.8   
3          3011524                       40.1                9.3   
4         39538223                       40.7                7.8   

   cardiac_mortality_rate  high_bp_prevalence  copd_prevalence  \
0                   289.3                39.4              9.3   
1                   178.5                32.8              4.6   
2                   181.8                29.9              6.0   
3                   284.3                38.2              9.7   
4                   192.5                26.6              4.2   

   kidney_disease_prevalence  diabetes_prevalence  Physicians  \
0                        3.1                 12.2     10983.0   
1                        1.8                  7.1      2101.0   
2                        3.6                  9.8     18343.0   
3                        3.7                 12.2      6500.0   
4                        2.8                  9.4    113718.0   

   Physicians Rate  Active MO  Active MO Rate  Active DO  Active DO Rate  \
0            224.0    10389.0           211.9      594.0            12.1   
1            287.2     1825.0           249.5      276.0            37.7   
2            252.0    15989.0           219.7   

In [268]:
miss_data = df[df['Location'] == 'Mississippi']
miss_data

Location  Employment_2020  Employment_2021  Employment_2022  \
23  Mississippi          1573290          1625695          1674142   

    Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  Life_Exp_2020  \
23             42513             46577             46370           71.9   

    Life_Exp_2019  Life_Exp_2018  Employer_2019  Non-Group_2019  \
23           74.4           74.6          0.422           0.047   

    Medicaid_2019  Medicare_2019  Military_2019  Uninsured_2019  \
23          0.242          0.142          0.018           0.129   

    Employer_2021  Non-Group_2021  Medicaid_2021  Medicare_2021  \
23          0.421           0.055           0.24          0.145   

    Military_2021  Uninsured_2021  Population Density per mi²  \
23           0.02           0.119                       63.07   

    2010 Population  2020 Population  flu_vaccination_rate_2019  \
23          2967297          2961279                       37.3   

    asthma_prevalence  cardiac_mortality_rate  high_bp_prevalence  \
23                9.8                   299.6                41.2   

    copd_prevalence  kidney_disease_prevalence  diabetes_prevalence  \
23              8.8                        2.7                 13.4   

    Physicians  Physicians Rate  Active MO  Active MO Rate  Active DO  \
23      5857.0            196.8     5370.0           180.4      487.0   

    Active DO Rate  Exc_deaths_2017  Exc_deaths_2018  Exc_deaths_2019  \
23            16.4             1236             2238             1809   

    Exc_deaths_2020  Exc_deaths_2021  Exc_deaths_2022  Dist_Per_100K_2021_x  \
23            16039            18507            10467                154010   

    Distributed_Per_100k_65Plus_2021_x  Admin_Per_100K_2021_x  \
23                              941780                 113848   

    Admin_Per_100k_65Plus_2021_x  Administered_Dose1_Pop_Pct_2021_x  \
23                        210412                               55.3   

    Administered_Dose1_Recip_65PlusPop_Pct_2021_x  \
23                                           89.1   

    Series_Complete_Pop_Pct_2021_x  Series_Complete_65PlusPop_Pct_2021_x  \
23                            48.1                                  81.7   

    Additional_Doses_Vax_Pct_2021_x  Additional_Doses_50Plus_Vax_Pct_2021_x  \
23                             24.8                                    37.3   

    Additional_Doses_65Plus_Vax_Pct_2021_x  Dist_Per_100K_2022_x  \
23                                    48.2                234096   

    Distributed_Per_100k_65Plus_2022_x  Admin_Per_100K_2022_x  \
23                             1431510                 142742   

    Admin_Per_100k_65Plus_2022_x  Administered_Dose1_Pop_Pct_2022_x  \
23                        269552                               61.5   

    Administered_Dose1_Recip_65PlusPop_Pct_2022_x  \
23                                           93.6   

    Series_Complete_Pop_Pct_2022_x  Series_Complete_65PlusPop_Pct_2022_x  \
23                            53.6                                  86.0   

    Additional_Doses_Vax_Pct_2022_x  Additional_Doses_50Plus_Vax_Pct_2022_x  \
23                             40.9                                    56.8   

    Additional_Doses_65Plus_Vax_Pct_2022_x  Second_Booster_50Plus_Vax_Pct_x  \
23                                    66.7                             37.3   

    Second_Booster_65Plus_Vax_Pct_x  Bivalent_Booster_65Plus_Pop_Pct_x  \
23                             43.2                               18.4   

    astha_prevalence  Dist_Per_100K_2021_y  \
23             False                154010   

    Distributed_Per_100k_65Plus_2021_y  Admin_Per_100K_2021_y  \
23                              941780                 113848   

    Admin_Per_100k_65Plus_2021_y  Administered_Dose1_Pop_Pct_2021_y  \
23                        210412                               55.3   

    Administered_Dose1_Recip_65PlusPop_Pct_2021_y  \
23                                           89.1   

    

## Model

In [281]:
%%time
fgrad = GradientBoostingRegressor(learning_rate = 0.1, max_depth = 1, n_estimators = 200)
fmulti = MultiOutputRegressor(fgrad)
fmulti.fit(X_train_polysc, y_train)

fmulti.score(X_train_polysc, y_train), fmulti.score(X_test_polysc, y_test)

CPU times: user 7.29 s, sys: 12.5 ms, total: 7.3 s
Wall time: 7.38 s


(0.9999918872830208, 0.9189772379140231)

In [304]:
feature_importances = [est.feature_importances_ for est in fmulti.estimators_]
feature_names = poly.get_feature_names_out(X1.columns)

importances_df = pd.DataFrame(
    data=feature_importances,
    columns=feature_names
)
mean_importance = pd.DataFrame(importances_df.mean().sort_values(ascending=False))
mean_importance

0
Physicians Go to a cafe, bar, or restaurant         7.767258e-02
2010 Population Additional_Doses_Vax_Pct_2022_y     4.293934e-02
2020 Population Go to work                          4.075023e-02
Employment_2022 Second_Booster_65Plus_Vax_Pct_x     4.017795e-02
Non-Group_2019 Uninsured_2019                       3.865743e-02
Employment_2021 copd_prevalence                     3.551425e-02
high_bp_prevalence Physicians                       3.500318e-02
2020 Population diabetes_prevalence                 3.419426e-02
Employment_2021 Go to work                          3.329587e-02
high_bp_prevalence Additional_Doses_Vax_Pct_2022_x  3.131252e-02
2020 Population Been in a room with someone out...  2.983305e-02
2020 Population Administered_Dose1_Pop_Pct_2022_y   2.947771e-02
2010 Population Been in a room with someone out...  2.837290e-02
2010 Population copd_prevalence                     2.404017e-02
Employment_2020 Been in a room with someone out...  2.382027e-02
Employment_2021 Frequently washing hands            2.305212e-02
Employment_2020 Active DO Rate                      2.262427e-02
diabetes_prevalence Physicians                      2.101830e-02
kidney_disease_prevalence Physicians                1.862138e-02
2020 Population copd_prevalence                     1.724397e-02
Employment_2021 Military_2021                       1.716138e-02
2020 Population kidney_disease_prevalence           1.554846e-02
Active DO Go to the gym                             1.534351e-02
2010 Population Go to church or another place o...  1.491092e-02
Employment_2022 Dist_Per_100K_2021_x                1.445401e-02
Employment_2022 copd_prevalence                     1.399797e-02
2010 Population diabetes_prevalence                 1.355641e-02
Physicians Go to work                               1.321877e-02
Uninsured_2019 2010 Population                      1.196198e-02
2010 Population high_bp_prevalence                  1.166474e-02
2010 Population 2020 Population                     1.102755e-02
Employment_2020 cardiac_mortality_rate              1.062732e-02
Active DO Go to a doctor or visit a hospital        9.226870e-03
Employment_2021 Admin_Per_100K_2022_y               9.041099e-03
Employment_2020 Go to work                          9.031382e-03
Employment_2022 Go to work                          8.604656e-03
Employment_2021 cardiac_mortality_rate              7.653816e-03
Active MO Go to the gym                             7.417848e-03
Physicians Go to a doctor or visit a hospital       7.375215e-03
2010 Population Current President                   7.283154e-03
2020 Population Go visit a friend                   6.627339e-03
Employment_2022 Yes, 11-50 people                   6.488215e-03
Employment_2020 Uninsured_2019                      5.106814e-03
Military_2021 Active MO                             4.873333e-03
Employment_2020 high_bp_prevalence                  4.784130e-03
kidney_disease_prevalence Active MO                 4.224547e-03
Employment_2020 copd_prevalence                     4.108998e-03
Uninsured_2021 Wearing a face mask when outside...  4.068239e-03
Medicare_2019 2010 Population                       3.976806e-03
Employment_2021 Non-Group_2019                      3.814723e-03
Employment_2022 Medicaid_2019                       3.712408e-03
Uninsured_2019 Active DO                            3.503450e-03
Uninsured_2019 Active MO                            2.915641e-03
Uninsured_2021 Distributed_Per_100k_65Plus_2022_y   2.881988e-03
Medicaid_2019 Physicians                            2.833210e-03
2010 Population Go to work                          2.769935e-03
Employment_2020 Medicaid_2021                       2.665156e-03
Employment_2021 Series_Complete_65PlusPop_Pct_2...  2.502140e-03
Uninsured_2019 Physicians                           2.412045e-03
2010 Population kidney_disease_prevalence           2.203962e-03
Employment_2022 Been in a room with someone out...  2.149081e-03
asthma_prevalence Admin_Per_100k_

In [309]:
test_data = pd.read_csv('Data/Test_Data/state_test_data.csv')
test_data.head()

Location          Change  Employment_2020  Employment_2021  \
0  Mississippi        Original          1573290          1625695   
1  Mississippi            Mask          1573290          1625695   
2  Mississippi  Visit a friend          1573290          1625695   
3  Mississippi   Dose_pop_2021          1573290          1625695   
4  Mississippi    Wearing mask          1573290          1625695   

   Employment_2022  Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  \
0          1674142             42513             46577             46370   
1          1674142             42513             46577             46370   
2          1674142             42513             46577             46370   
3          1674142             42513             46577             46370   
4          1674142             42513             46577             46370   

   Life_Exp_2020  Life_Exp_2019  Life_Exp_2018  Employer_2019  Non-Group_2019  \
0           71.9           74.4           74.6          0.422           0.047   
1           71.9           74.4           74.6          0.422           0.047   
2           71.9           74.4           74.6          0.422           0.047   
3           71.9           74.4           74.6          0.422           0.047   
4           71.9           74.4           74.6          0.422           0.047   

   Medicaid_2019  Medicare_2019  Military_2019  Uninsured_2019  Employer_2021  \
0          0.242          0.142          0.018           0.129          0.421   
1          0.242          0.142          0.018           0.129          0.421   
2          0.242          0.142          0.018           0.129          0.421   
3          0.242          0.142          0.018           0.129          0.421   
4          0.242          0.142          0.018           0.129          0.421   

   Non-Group_2021  Medicaid_2021  Medicare_2021  Military_2021  \
0           0.055           0.24          0.145           0.02   
1           0.055           0.24          0.145           0.02   
2           0.055           0.24          0.145           0.02   
3           0.055           0.24          0.145           0.02   
4           0.055           0.24          0.145           0.02   

   Uninsured_2021  Population Density per mi²  2010 Population  \
0           0.119                       63.07          2967297   
1           0.119                       63.07          2967297   
2           0.119                       63.07          2967297   
3           0.119                       63.07          2967297   
4           0.119                       63.07          2967297   

   2020 Population  flu_vaccination_rate_2019  asthma_prevalence  \
0          2961279                       37.3                9.8   
1          2961279                       37.3                9.8   
2          2961279                       37.3                9.8   
3          2961279                       37.3                9.8   
4          2961279                       37.3                9.8   

   cardiac_mortality_rate  high_bp_prevalence  copd_prevalence  \
0                   299.6                41.2              8.8   
1                   299.6                41.2              8.8   
2                   299.6                41.2              8.8   
3                   299.6                41.2              8.8   
4                   299.6                41.2              8.8   

   kidney_disease_prevalence  diabetes_prevalence  Physicians  \
0                        2.7                 13.4        5857   
1                        2.7                 13.4        5857   
2                        2.7                 13.4        5857   
3                        2.7                 13.4        5857   
4                        2.7                 13.4        5857   

   Physicians Rate  Active MO  Active MO Rate  Active DO  Active DO Rate  \
0            196.8       5370           180.4        487            16.4   
1            196.8     

In [314]:
test_x = test_data.drop(columns=['Location', 'Change', 'Mask_Mandate'])
test_xpoly = poly.transform(test_x)
test_x_polysc = ss.transform(test_xpoly)

In [329]:
y_pred = pd.DataFrame(fmulti.predict(test_x_polysc))
results = test_data[['Location', 'Change']]
results = pd.merge(results, y_pred, left_index=True, right_index=True)
results.rename(columns={0: 'covid_deaths_2020', 1: 'covid_deaths_2021', 2: 'covid_deaths_2022'}, inplace=True)
results

Location          Change  covid_deaths_2020  covid_deaths_2021  \
0     Mississippi        Original        4906.910915        5872.654510   
1     Mississippi            Mask        4906.910915        5876.984386   
2     Mississippi  Visit a friend        4906.910915        5872.654510   
3     Mississippi   Dose_pop_2021        4906.910915        5872.654510   
4     Mississippi    Wearing mask        4906.910915        5872.654510   
5     Mississippi     All Changes        4906.910915        5876.984386   
6   West Virginia        Original        1348.695136        3834.794277   
7   West Virginia            Mask        1348.695136        3830.464401   
8   West Virginia  Visit a friend        1482.877408        3853.630124   
9   West Virginia   Dose_pop_2021        1348.695136        3834.794277   
10  West Virginia    Wearing mask        1348.695136        3834.794277   
11  West Virginia     All Changes        1482.877408        3853.630124   
12       Oklahoma        Original        4625.182670        7316.664116   
13       Oklahoma            Mask        4625.182670        7316.664116   
14       Oklahoma  Visit a friend        4789.920783        7316.664116   
15       Oklahoma   Dose_pop_2021        4625.182670        7316.664116   
16       Oklahoma    Wearing mask        4625.182670        8859.280062   
17       Oklahoma     All Changes        4789.920783        8859.280062   
18        Alabama        Original        6339.231336        9768.347252   
19        Alabama            Mask        6339.231336        9764.017377   
20        Alabama  Visit a friend        6377.046656        9787.183100   
21        Alabama   Dose_pop_2021        6339.231336        9768.347252   
22        Alabama    Wearing mask        6339.231336        9768.347252   
23        Alabama     All Changes        6377.046656        9787.183100   
24      Tennessee        Original        7325.012530       13264.080744   
25      Tennessee            Mask        7325.012530       13268.410619   
26      Tennessee  Visit a friend        7329.155913       13264.080744   
27      Tennessee   Dose_pop_2021        7325.012530       13264.080744   
28      Tennessee    Wearing mask        7325.012530       13264.080744   
29      Tennessee     All Changes        7329.155913       13268.410619   

    covid_deaths_2022  
0         3055.783445  
1         3055.783445  
2         3055.783445  
3         3055.783445  
4         3050.447947  
5         3050.447947  
6         2217.510485  
7         2217.510485  
8         2217.510485  
9         2217.510485  
10        2212.174987  
11        2212.174987  
12        4313.156379  
13        4313.156379  
14        4313.156379  
15        4313.156379  
16        4478.811885  
17        4478.811885  
18        3960.056729  
19        3960.056729  
20        3960.056729  
21        3960.056729  
22        3960.056729  
23        3960.056729  
24        6517.391226  
25        6517.391226  
26        6517.391226  
27        6517.391226  
28        6512.055728  
29        6512.055728